In [ ]:
%matplotlib notebook

import numpy as np
from scipy.integrate import odeint
import matplotlib.pyplot as plt
from matplotlib import animation
plt.rcParams["animation.html"] = "jshtml"

In [ ]:
m1 = 1
m2 = 1
c1 = 0.1
c2 = 0.1
c3 = 0.1
a1 = 0.1
a2 = 0.1
a3 = 0.1
k1 = 0.05
k2 = 0.21
k3 = 0.11
C1 = 0.15
C2 = 0.30
omega = 0.1

f1 = lambda t: C1*np.cos(omega*t)
f2 = lambda t: C2*np.cos(omega*t)

def deriv(X, t):
    """Return the derivatives dx/dt and d2x/dt2."""
    x1, x2, xd1, xd2 = X
    F1 = f1(t)
    F2 = f2(t)
    xdd1 = F1 - xd1*(c1 + c2) + xd2*c2 - x1*(k1 + k2) + x2*k2 - a1*x1**3 + a2*(x2 - x1)**3
    xdd2 = F2 - xd2*(c2 + c3) + xd1*c1 - x2*(k2 + k3) + x1*k2 - a3*x2**3 + a2*(x2 - x1)**3
    return xd1, xd2, xdd1/m1, xdd2/m2


def solve_duffing(tmax, dt_per_period, t_trans, x0, v0):
    """Solve the Duffing equation with the standard odeint solver.
    
    Find the numerical solution to the Duffing equation using a suitable
    time grid: tmax is the maximum time (s) to integrate to; t_trans is
    the initial time period of transient behaviour until the solution
    settles down (if it does) to some kind of periodic motion (these data
    points are dropped) and dt_per_period is the number of time samples
    (of duration dt) to include per period of the driving motion (frequency
    omega).
    
    Returns the time grid, t (after t_trans), position, x, and velocity,
    xdot, dt, and step, the number of array points per period of the driving
    motion.
    
    """
    # Time point spacings and the time grid

    period = 2*np.pi/omega
    dt = 2*np.pi/omega / dt_per_period
    step = int(period / dt)
    t = np.arange(0, tmax, dt)
    # Initial conditions: x, xdot
    X0 = x0 + v0
    X = odeint(deriv, X0, t)
    idx = int(t_trans / dt)
    return t[idx:], X[idx:], dt, step

In [ ]:
# Set up the motion for a oscillator with initial positions and velocities
x0, v0 = (0.5, -0.5), (0.5, -0.1)
tmax, t_trans = 150, 0
dt_per_period = 100

In [ ]:
# Solve the equation of motion.
t, X, dt, pstep = solve_duffing(tmax, dt_per_period, t_trans, x0, v0)
print("# samples: %d" % len(t))
print("dt: %.4f" % dt)
print("Steps per period: %d" % pstep)
x1, x2, xd1, xd2 = X.T

In [ ]:
fig1, ((ax11, ax12), (ax21, ax22)) = plt.subplots(nrows=2, ncols=2)

ax11.plot(t, x1)
ax11.set_xlabel(r'$x_1$')
ax12.plot(t, x2)
ax12.set_xlabel(r'$x_2$')
ax21.plot(t, xd1)
ax21.set_xlabel(r'$v_1$')
ax22.plot(t, xd2)
ax22.set_xlabel(r'$v_2$')
plt.tight_layout()

In [ ]:
%%capture
fig2, ((ax11, ax12), (ax21, ax22)) = plt.subplots(nrows=2, ncols=2)

# Positions
ax11.set_xlabel(r'$x_1$')
ax11.set_ylabel(r'$x_2$')
ln11, = ax11.plot([], [])
ax11.set_xlim([np.min(x1), np.max(x1)])
ax11.set_ylim([np.min(x2), np.max(x2)])

# Velocities
ax12.set_xlabel(r'$v_1$')
ax12.set_ylabel(r'$v_2$')
ln12, = ax12.plot([], [])
ax12.set_xlim([np.min(xd1), np.max(xd1)])
ax12.set_ylim([np.min(xd2), np.max(xd2)])

# Phase spaces
ax21.set_xlabel(r'$\mathbf{x}$')
ax21.set_ylabel(r'$\mathbf{v}$')
ln21a, = ax21.plot([], [])
ln21b, = ax21.plot([], [])
ax21.set_xlim([min(np.min(x1), np.min(x2)), max(np.max(x1), np.max(x2))])
ax21.set_ylim([min(np.min(xd1), np.min(xd2)), max(np.max(xd1), np.max(xd2))])

# F(t)
F1 = f1(t)
F2 = f2(t)
ax22.set_xlabel(r'$t$')
ax22.set_ylabel(r'$\mathbf{F}(t)$')
ln22a, = ax22.plot([], [])
ln22b, = ax22.plot([], [])
ax22.set_xlim([t[0], t[-1]])
ax21.set_ylim([min(np.min(F1), np.min(F2)), max(np.max(F1), np.max(F2))])

plt.tight_layout()

def animate(i):
    ln11.set_data(x1[:i], x2[:i])
    ln12.set_data(xd1[:i], xd2[:i])
    ln21a.set_data(x1[:i], xd1[:i])
    ln21b.set_data(x2[:i], xd2[:i])
    ln22a.set_data(t[:i], F1[:i])
    ln22b.set_data(t[:i], F2[:i])
    

anim = animation.FuncAnimation(fig2, animate, frames=len(t), interval=100, repeat_delay=1000)

In [ ]:
anim